In [1]:
# https://github.com/Kaggle/kaggle-environments/blob/master/kaggle_environments/envs/hungry_geese/hungry_geese.py

In [1]:
from kaggle_environments.envs.hungry_geese.hungry_geese import Observation, Configuration, Action, \
                                                                row_col, adjacent_positions, translate, min_distance

from kaggle_environments import make
from random import choice
import numpy as np

import pickle

Loading environment football failed: No module named 'gfootball'


In [2]:
import numpy as np
import random
import keras
from keras.models import Sequential
from keras.layers import Dense, Dropout
from keras.optimizers import Adam

from collections import deque

In [5]:
def geese_heads(obs_dict, config_dict):
    """
    Return the position of the geese's heads
    """
    configuration = Configuration(config_dict)

    observation = Observation(obs_dict)
    player_index = observation.index
    player_goose = observation.geese[player_index]
    player_head = player_goose[0]
    player_row, player_column = row_col(player_head, configuration.columns)
    positions = []
    for geese in observation.geese:
        if len(geese)>0:
            geese_head = geese[0]
            row, column = row_col(geese_head, configuration.columns)
        else:
            row = None
            column = None
        positions.append((row, column))
    return positions

def get_last_actions(previous_geese_heads, heads_positions):

    def get_last_action(prev, cur):
        last_action = None

        prev_row = prev[0]
        prev_col = prev[1]
        cur_row = cur[0]
        cur_col = cur[1]

        if cur_row is not None:
            if (cur_row-prev_row == 1) | ((cur_row==0) & (prev_row==6)):
                last_action = Action.SOUTH.name
            elif (cur_row-prev_row == -1) | ((cur_row==6) & (prev_row==0)):
                last_action = Action.NORTH.name
            elif (cur_col-prev_col == 1) | ((cur_col==0) & (prev_col==10)):
                last_action = Action.EAST.name
            elif (cur_col-prev_col == -1) | ((cur_col==10) & (prev_col==0)):
                last_action = Action.WEST.name

        return last_action

    if len(previous_geese_heads) == 0:
        actions = [Action.SOUTH.name, Action.NORTH.name, Action.EAST.name, Action.WEST.name]
        nb_geeses = len(heads_positions)
        last_actions = [actions[np.random.randint(4)] for _ in range(nb_geeses)]
    else:   
        last_actions = [get_last_action(*pos) for pos in zip(previous_geese_heads, heads_positions)]

    return last_actions
    
def central_state_space(obs_dict, config_dict, prev_head):
    """
    Recreating a board where my agent's head in the middle of the board 
    (position (4,5)), and creating features accordingly
    """
    
    configuration = Configuration(config_dict)

    observation = Observation(obs_dict)
    player_index = observation.index
    player_goose = observation.geese[player_index]
    if len(player_goose)==0:
        player_head = prev_head
    else:
        player_head = player_goose[0]
    player_row, player_column = row_col(player_head, configuration.columns)
    row_offset = player_row - 3
    column_offset = player_row - 5

    foods = observation['food']

    def centralize(row, col):
        if col > player_column:
            new_col = (5 + col - player_column) % 11
        else:
            new_col = 5 - (player_column - col)
            if new_col < 0:
                new_col += 11

        if row > player_row:
            new_row = (3 + row - player_row) % 7
        else:
            new_row = 3 - (player_row - row)
            if new_row < 0:
                new_row += 7
        return new_row, new_col

    food1_row, food1_column = centralize(*row_col(foods[0], configuration.columns))
    food2_row, food2_column = centralize(*row_col(foods[1], configuration.columns))

#     food1_row_feat = float(food1_row - 3)/3 if food1_row>=3 else float(food1_row - 3)/3
#     food2_row_feat = float(food2_row - 3)/3 if food2_row>=3 else float(food2_row - 3)/3

#     food1_col_feat = float(food1_column - 5)/5 if food1_column>=5 else float(food1_column - 5)/5
#     food2_col_feat = float(food2_column - 5)/5 if food2_column>=5 else float(food2_column - 5)/5

    # Create the grid
    board = np.zeros([7, 11])
    # Add food to board
    board[food1_row, food1_column] = 1
    board[food2_row, food2_column] = 1

    for goose in observation.geese:
        if len(goose)>0:
            for pos in goose:
                # set bodies to 1
                row, col = centralize(*row_col(pos, configuration.columns))
                board[row, col]=-0.5
                # Set head to five
            row, col = centralize(*row_col(goose[0], configuration.columns))
            board[row,col]=-1
            # Just make sure my goose head is 0
            board[3, 5] = 0
                    
            
    return board #,len(player_goose), food1_row_feat, food1_col_feat, food2_row_feat, food2_col_feat

In [11]:
class StateTranslator_Central:
    """
    Returns a board where we are always at the center
    """
    
    def __init__(self):
        
        self.last_action = None
        self.step_count = 0
        self.last_goose_length = 1
        self.last_goose_ind = 0
        self.observations = []
        
    def set_last_action(self, last_action):
        self.last_action = last_action
        
        
    def __get_last_action_vec(self):
        action_vec = np.zeros(4)
        
        if self.last_action == 'NORTH':
            action_vec[0] = 1
        elif self.last_action == 'SOUTH':
            action_vec[1] = 1
        elif self.last_action == 'EAST':
            action_vec[2] = 1
        elif self.last_action == 'WEST':
            action_vec[3] = 1
        
        return action_vec
    
    def translate_action_to_text(self, action):
        
        h = {0 : 'WEST',
             1: 'EAST',
             2: 'NORTH',
             3: 'SOUTH'}
        
        return h[action]

    def translate_text_to_int(self, action):
        h = {'WEST':0,
            'EAST':1,
            'NORTH':2,
            'SOUTH':3}
        
        return h[action]
    
    
    def update_length(self):
        self.last_goose_length = self.current_goose_length
        
    
    def get_state(self, observation, config):
        
        board = central_state_space(observation, config, self.last_goose_ind)
        self.step_count = observation['step']
        
        geese = observation['geese']
        self.current_goose_length = len(geese[observation['index']])  
        
        #### This is exception handling for if our goose died this turn, to use the last
        ### known index as its postion for the state centralizer
        if len(geese[observation['index']])>1:
            self.last_goose_ind = geese[observation['index']][0]
            
        ####
        biggest_goose = 0
        alive_geese = 0
        for ind, goose in enumerate(geese):
            if len(goose)>biggest_goose:
                biggest_goose = len(goose)
            if ind != observation['index'] and len(goose)>0:
                alive_geese+=1
        
        state = np.array([])
        state = np.append(state, self.__get_last_action_vec())
        state = np.append(state, self.current_goose_length/15)
        state = np.append(state, biggest_goose/15)
        state = np.append(state, alive_geese/8)
        state = np.append(state, self.step_count/200)
        state = np.append(state, board.flatten())
        
        state = state.flatten()
        self.update_length()
        
        return state
    
    def calculate_reward(self, observation):
        
        current_geese = observation['geese']
        prev = self.last_goose_length
        cur = len(current_geese[observation['index']])  
        
        reward = -1       
    
        ### If we grow, reward is 100
        if cur>prev:
            reward = 100
        
        else:
            reward = -1
        
        ### If we die -150
        if cur == 0:
            reward = -150
            
        ### see if any geese are alive

        alive_geese = 0
        for ind, goose in enumerate(current_geese):
            if ind != observation['index'] and len(goose)>0:
                alive_geese+=1
        
        # If we are the last one standing
        if alive_geese == 0 and cur>0:
            reward = 500
            
        ### if the game ends and we are the biggest
        if self.step_count == 200:
            biggest_goose = 0
            biggest_goose_ind = None
            for ind, goose in enumerate(current_geese):
                if len(goose)>biggest_goose:
                    biggest_goose = len(goose)
                    biggest_goose_ind = ind
            
            if biggest_goose_ind == observation['index']:
                reward = 500
        
        return reward
        

In [35]:
class dqnAgent:
    """
    Given an environment state, choose an action, and learn from the reward
    https://towardsdatascience.com/reinforcement-learning-w-keras-openai-dqns-1eed3a5338c
    https://towardsdatascience.com/deep-q-learning-tutorial-mindqn-2a4c855abffc
    https://www.researchgate.net/post/What-are-possible-reasons-why-Q-loss-is-not-converging-in-Deep-Q-Learning-algorithm
    """

    def __init__(self, model=None, epsilon = 1.0, epsilon_min = 0.15):

        self.StateTrans = StateTranslator_Central()
        self.state_shape  = 85
        print('my state shape is:', self.state_shape)
        self.memory  = deque(maxlen=2000)
        self.gamma = 0.95
        self.epsilon = epsilon
        self.epsilon_min = epsilon_min
        self.epsilon_decay = 0.990
        self.learning_rate = 0.001
        self.tau = .125

        if model == None:
            self.model = self.create_model()
        else:
            self.model = model
        self.target_model = self.create_model()

    def create_model(self):
        model   = Sequential()
        model.add(Dense(2000, input_dim=self.state_shape, activation="relu"))
        model.add(Dense(1000, activation="relu"))
        model.add(Dense(500, activation="relu"))
        model.add(Dense(1000, activation="relu"))
        model.add(Dense(500, activation="relu"))
        model.add(Dense(100, activation="relu"))
        model.add(Dense(4))
        model.compile(loss="MSE",
            optimizer=Adam(lr=self.learning_rate))
        return model

    def act(self, state):
        self.epsilon *= self.epsilon_decay
        self.epsilon = max(self.epsilon_min, self.epsilon)
        if np.random.random() < self.epsilon:
            # Set random choice to north or east as the agent is not moving in these directions
            return random.choice([0,1,2,3])

        action_values = self.model.predict(state.reshape(-1, self.state_shape))[0]
        action = np.argmax(action_values)

        return action
    
    def translate_state(self, observation, configuration):
        state = self.StateTrans.get_state(observation, configuration)
        return state

    def __call__(self, observation, configuration):
        
        state = self.translate_state(observation, configuration)
        action = self.act(state)
        # State translator will take in 0, 1, 2, 3 and return straight, left or right, which in turn will 
        # be translated into a kaggle Action
        action_text = self.StateTrans.translate_action_to_text(action)
        
        # Update our step number and actions
        self.StateTrans.update_step()
        self.StateTrans.set_last_action(action_text)
        
        return action_text
    
    def remember(self, state, action, reward, new_state, done):
        self.memory.append([state, action, reward, new_state, done])

    def replay(self):
        batch_size = 32
        if len(self.memory) < batch_size:
            return

        samples = random.sample(self.memory, batch_size)
        ########################
        # This can be sped up significantly, but processing all samples in batch rather than 1 at a time
        ####################
        for sample in samples:
            state, action, reward, new_state, done = sample
            target = self.target_model.predict(state.reshape(-1, self.state_shape))
            if done:
                target[0][action] = reward
            else:
                Q_future = max(self.target_model.predict(new_state.reshape(-1, self.state_shape))[0])
                target[0][action] = reward + Q_future * self.gamma
            self.model.fit(state.reshape(-1, self.state_shape), target, epochs=1, verbose=0)

    def target_train(self):
        weights = self.model.get_weights()
        target_weights = self.target_model.get_weights()
        for i in range(len(target_weights)):
            target_weights[i] = weights[i] * self.tau + target_weights[i] * (1 - self.tau)
        self.target_model.set_weights(target_weights)

    def save_model(self, fn):
        self.model.save(fn)


### Training script

In [36]:
steps_per_ep = 200
num_episodes = 10000

env = make("hungry_geese", debug=True)
config = env.configuration
train_name = 'central_agent'
model = keras.models.load_model('central_agent/trial-4620')

dqn = dqnAgent(model = model, epsilon = 0.95, epsilon_min = 0.15)
agent2 = GreedyAgent()
agent3 = GreedyAgent()
agent4 = GreedyAgent()

agents = [dqn, agent2, agent3, agent4]

results_dic = {}
for ep in range(num_episodes):
    
    print('episode number: ', ep+4620)
    state_dict = env.reset(num_agents=4)[0]
    observation = state_dict['observation']
    my_goose_ind = observation['index']
    
    action = state_dict['action']
    
    dqn.StateTrans.set_last_action(None)
    dqn.StateTrans.step_count = 0
    dqn.StateTrans.last_goose_length = 1
    cur_state = dqn.StateTrans.get_state(observation, config)
    
    
    done = False
    for step in range(steps_per_ep):
        actions = []
        for agent in agents:
            action = agent(observation, config)
            actions.append(action)
        
        state_dict = env.step(actions)[0]
        observation = state_dict['observation']
        print(observation)
        
        action = state_dict['action']
        status = state_dict['status']
        
        
        action_for_model = dqn.StateTrans.translate_text_to_int(action)
        new_state = dqn.StateTrans.get_state(observation, config)
        
        # Set rewards based on if value was gained or lost
        reward = dqn.StateTrans.calculate_reward(observation)
        # Update our goose length based on prev state
        dqn.StateTrans.update_length()
       

        if status != "ACTIVE":
            done = True
        
        
        #Temp for just training agent to go get food
        
#         if reward<-1:
#             reward = -1
        print('reward: ', reward)
        dqn.remember(cur_state, action_for_model, reward, new_state, done)
        
        cur_state = new_state
            
        # Check if my goose died

            
        if done:
            print('Done, Step: ', step)
            print('status, ', status)
            results_dic[ep] = reward
            
            if ep % 100 == 0:
                directory = train_name
                dqn.save_model(directory + f"/trial-{ep+4620}")
                with open(directory + "/results_dic.pkl", 'wb') as f:
                    pickle.dump(results_dic, f)
            break
        

        if step%5 == 0:
            dqn.replay()        
            dqn.target_train()

#         if step%50 == 0:
#             print(f'We survived {step} steps')
#             directory = train_name
#             dqn.save_model(directory + f"/trial-{ep}")
        


my state shape is: 85
episode number:  4620
{'remainingOverageTime': 60, 'step': 1, 'geese': [[43], [24], [15], [5]], 'food': [73, 39], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 2, 'geese': [[32], [23], [14], [4]], 'food': [73, 39], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 3, 'geese': [[21], [34], [25], [15]], 'food': [73, 39], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 4, 'geese': [[11], [45], [36], [26]], 'food': [73, 39], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 5, 'geese': [[0], [44], [35], [25]], 'food': [73, 39], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 6, 'geese': [[66], [33], [24], [14]], 'food': [73, 39], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 7, 'geese': [[55], [43], [23], [13]], 'food': [73, 39], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 8, 'geese': [[44], [42], [22], [12]], 'food': [73, 39], 'index': 0}
reward:  -1
{'remainingOverageTime'

{'remainingOverageTime': 60, 'step': 2, 'geese': [[23], [55], [15], [60]], 'food': [57, 8], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 3, 'geese': [[24], [56], [16], [61]], 'food': [57, 8], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 4, 'geese': [[13], [67], [27], [72]], 'food': [57, 8], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 5, 'geese': [[2], [1], [38], [6]], 'food': [57, 8], 'index': 0}
reward:  -1
Opposite action: (0, <Action.SOUTH: 3>, <Action.NORTH: 1>)
{'remainingOverageTime': 60, 'step': 6, 'geese': [[], [12], [49], [17]], 'food': [57, 8], 'index': 0}
reward:  -150
Done, Step:  5
status,  DONE
episode number:  4631
{'remainingOverageTime': 60, 'step': 1, 'geese': [[53], [37], [4, 3], [55]], 'food': [66, 61], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 2, 'geese': [[42], [48], [15, 4], [66, 55]], 'food': [61, 70], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 3, 'geese': [[31], [59], [26, 15]

Opposite action: (0, <Action.WEST: 4>, <Action.EAST: 2>)
{'remainingOverageTime': 60, 'step': 12, 'geese': [[], [31], [29], [62]], 'food': [34, 63], 'index': 0}
reward:  -150
Done, Step:  11
status,  DONE
episode number:  4637
{'remainingOverageTime': 60, 'step': 1, 'geese': [[65], [41], [44], [47]], 'food': [7, 50], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 2, 'geese': [[76], [40], [54], [46]], 'food': [7, 50], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 3, 'geese': [[10], [51], [65], [57]], 'food': [7, 50], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 4, 'geese': [[9], [50, 51], [64], [56]], 'food': [7, 19], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 5, 'geese': [[20], [61, 50], [75], [67]], 'food': [7, 19], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 6, 'geese': [[31], [60, 61], [74], [66]], 'food': [7, 19], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 7, 'geese': [[42], [49, 60], 

{'remainingOverageTime': 60, 'step': 2, 'geese': [[22], [25], [0, 10], [38]], 'food': [39, 1], 'index': 0}
reward:  -1
Opposite action: (0, <Action.WEST: 4>, <Action.EAST: 2>)
{'remainingOverageTime': 60, 'step': 3, 'geese': [[], [26], [1, 0, 10], [39, 38]], 'food': [47, 11], 'index': 0}
reward:  -150
Done, Step:  2
status,  DONE
episode number:  4645
{'remainingOverageTime': 60, 'step': 1, 'geese': [[5], [65], [70], [67]], 'food': [29, 53], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 2, 'geese': [[6], [55], [71], [68]], 'food': [29, 53], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 3, 'geese': [[7], [56], [72], [69]], 'food': [29, 53], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 4, 'geese': [[18], [67], [6], [3]], 'food': [29, 53], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 5, 'geese': [[29, 18], [1], [17], [14]], 'food': [53, 52], 'index': 0}
reward:  100
{'remainingOverageTime': 60, 'step': 6, 'geese': [[40, 29], [2

{'remainingOverageTime': 60, 'step': 2, 'geese': [[54], [62], [44], [3]], 'food': [13, 10], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 3, 'geese': [[65], [51], [33], [69]], 'food': [13, 10], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 4, 'geese': [[76], [40], [22], [58]], 'food': [13, 10], 'index': 0}
reward:  -1
Opposite action: (0, <Action.NORTH: 1>, <Action.SOUTH: 3>)
{'remainingOverageTime': 60, 'step': 5, 'geese': [[], [29], [11], [47]], 'food': [13, 10], 'index': 0}
reward:  -150
Done, Step:  4
status,  DONE
episode number:  4651
{'remainingOverageTime': 60, 'step': 1, 'geese': [[30], [5], [1], [49]], 'food': [3, 35], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 2, 'geese': [[31], [71], [67], [38]], 'food': [3, 35], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 3, 'geese': [[32], [60], [56], [27]], 'food': [3, 35], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 4, 'geese': [[22], [61], [57], [28]], 'f

...

{'remainingOverageTime': 60, 'step': 17, 'geese': [[68, 67, 66, 76], [37, 36, 35], [], [60]], 'food': [23, 30], 'index': 0}
reward:  100
{'remainingOverageTime': 60, 'step': 18, 'geese': [[57, 68, 67, 66], [48, 37, 36], [], [71]], 'food': [23, 30], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 19, 'geese': [[56, 57, 68, 67], [47, 48, 37], [], [70]], 'food': [23, 30], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 20, 'geese': [[45, 56, 57, 68], [36, 47, 48], [], [59]], 'food': [23, 30], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 21, 'geese': [[34, 45, 56, 57], [25, 36, 47], [], [48]], 'food': [23, 30], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 22, 'geese': [[23, 34, 45, 56, 57], [14, 25, 36], [], [37]], 'food': [30, 29], 'index': 0}
reward:  100
{'remainingOverageTime': 60, 'step': 23, 'geese': [[12, 23, 34, 45, 56], [15, 14, 25], [], [38]], 'food': [30, 29], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 2

Goose Collision: SOUTH
Goose Collision: NORTH
{'remainingOverageTime': 60, 'step': 2, 'geese': [[22], [], [], [14]], 'food': [60, 28], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 3, 'geese': [[11], [], [], [13]], 'food': [60, 28], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 4, 'geese': [[21], [], [], [12]], 'food': [60, 28], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 5, 'geese': [[10], [], [], [23]], 'food': [60, 28], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 6, 'geese': [[9], [], [], [34]], 'food': [60, 28], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 7, 'geese': [[75], [], [], [45]], 'food': [60, 28], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 8, 'geese': [[74], [], [], [44]], 'food': [60, 28], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 9, 'geese': [[63], [], [], [33]], 'food': [60, 28], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 10, 'geese': [

{'remainingOverageTime': 60, 'step': 2, 'geese': [[26], [57], [8], [15]], 'food': [74, 7], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 3, 'geese': [[15], [58], [9], [16]], 'food': [74, 7], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 4, 'geese': [[14], [47], [75], [5]], 'food': [74, 7], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 5, 'geese': [[25], [36], [64], [71]], 'food': [74, 7], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 6, 'geese': [[26], [25], [53], [60]], 'food': [74, 7], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 7, 'geese': [[27], [14], [42], [49]], 'food': [74, 7], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 8, 'geese': [[28], [3], [31], [38]], 'food': [74, 7], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 9, 'geese': [[29], [69], [20], [27]], 'food': [74, 7], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 10, 'geese': [[18], [58], [9], [16]], '

Goose Collision: SOUTH
{'remainingOverageTime': 60, 'step': 22, 'geese': [[71, 5, 4, 3, 14, 25], [], [], [21]], 'food': [42, 37], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 23, 'geese': [[60, 71, 5, 4, 3, 14], [], [], [20]], 'food': [42, 37], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 24, 'geese': [[59, 60, 71, 5, 4, 3], [], [], [9]], 'food': [42, 37], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 25, 'geese': [[48, 59, 60, 71, 5, 4], [], [], [75]], 'food': [42, 37], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 26, 'geese': [[37, 48, 59, 60, 71, 5, 4], [], [], [64]], 'food': [42, 30], 'index': 0}
reward:  100
{'remainingOverageTime': 60, 'step': 27, 'geese': [[38, 37, 48, 59, 60, 71, 5], [], [], [53]], 'food': [42, 30], 'index': 0}
reward:  -1
{'remainingOverageTime': 60, 'step': 28, 'geese': [[39, 38, 37, 48, 59, 60, 71], [], [], [42, 53]], 'food': [30, 40], 'index': 0}
reward:  -1
Opposite action: (0, <Action.WEST: 4>

KeyboardInterrupt: 

### Ideas for future improvement:
- Should be penalized harder for collision than starvation
- Add hunger feature

In [20]:
model = keras.models.load_model('central_agent/trial-453')


In [21]:
MyAgent = dqnAgent(model = model,
                   epsilon = 0,
                   epsilon_min = 0)

my state shape is: 85


In [22]:
env = make("hungry_geese", debug=True)


In [29]:
env.reset(num_agents=4)
results = env.run([MyAgent, GreedyAgent(), GreedyAgent(), GreedyAgent()])

Opposite action: (2, <Action.EAST: 2>, <Action.WEST: 4>)
Opposite action: (1, <Action.WEST: 4>, <Action.EAST: 2>)
Goose Collision: EAST


In [30]:
env.render(mode="ipython")

In [ ]:
results

In [ ]:
env.configuration